* LLM: https://huggingface.co/TheBloke/dolphin-2.2.1-mistral-7B-GGUF
* FlagEmbedding: https://huggingface.co/BAAI/bge-small-en-v1.5

# Libraries

_Python_ bindings for _llama.cpp_ does not include _GPU_ support without the required argument, it can be recompiled with the following command:
```sh
CMAKE_ARGS='-DLLAMA_CUBLAS=on' pip install --force-reinstall --no-cache-dir llama-cpp-python
```

In [1]:
from os                                  import environ
from llama_index                         import SimpleDirectoryReader, ServiceContext, VectorStoreIndex
from llama_index.embeddings              import HuggingFaceEmbedding
from llama_index.llms                    import LlamaCPP
from llama_index.llms.llama_utils        import (messages_to_prompt, completion_to_prompt)
from llama_index.storage.storage_context import StorageContext
from llama_index.vector_stores           import MilvusVectorStore

# Change Directory for Model Downloads

In [2]:
environ["LLAMA_INDEX_CACHE_DIR"] = "dist"

# Large Language Model

In [3]:
llm = LlamaCPP(
    completion_to_prompt=completion_to_prompt,
    context_window=3900,
    generate_kwargs={},
    max_new_tokens=256,
    messages_to_prompt=messages_to_prompt,
    model_kwargs={"n_gpu_layers": -1},
    model_url="https://huggingface.co/TheBloke/dolphin-2.2.1-mistral-7B-GGUF/resolve/main/dolphin-2.2.1-mistral-7b.Q4_K_M.gguf?download=true",
    temperature=0.1,
    verbose=True
)

ggml_init_cublas: GGML_CUDA_FORCE_MMQ:   no
ggml_init_cublas: CUDA_USE_TENSOR_CORES: yes
ggml_init_cublas: found 1 CUDA devices:
  Device 0: NVIDIA GeForce RTX 4070 Ti, compute capability 8.9
llama_model_loader: loaded meta data with 20 key-value pairs and 291 tensors from dist/models/dolphin-2.2.1-mistral-7b.Q4_K_M.gguf?download=true (version GGUF V3 (latest))
llama_model_loader: - tensor    0:                token_embd.weight q4_K     [  4096, 32002,     1,     1 ]
llama_model_loader: - tensor    1:              blk.0.attn_q.weight q4_K     [  4096,  4096,     1,     1 ]
llama_model_loader: - tensor    2:              blk.0.attn_k.weight q4_K     [  4096,  1024,     1,     1 ]
llama_model_loader: - tensor    3:              blk.0.attn_v.weight q6_K     [  4096,  1024,     1,     1 ]
llama_model_loader: - tensor    4:         blk.0.attn_output.weight q4_K     [  4096,  4096,     1,     1 ]
llama_model_loader: - tensor    5:            blk.0.ffn_gate.weight q4_K     [  4096, 14336,    

# FlagEmbedding

In [4]:
embedding = HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5")

# Milvus Vector Database

Of course! Must be running first, change to _Milvus_ directory and run with:
```sh
docker compose up
```

In [5]:
vector_store    = MilvusVectorStore(dim=384, overwrite=True)
storage_context = StorageContext.from_defaults(vector_store=vector_store)

# Load Documents from Directoy

In [6]:
loader = SimpleDirectoryReader('./data', recursive=True, exclude_hidden=True)

# Tying Everything Up

In [7]:
service_context = ServiceContext.from_defaults(llm=llm, embed_model=embedding)
documents       = loader.load_data()
index           = VectorStoreIndex.from_documents(documents, service_context=service_context, storage_context=storage_context)

# Query Engine

In [8]:
query_engine = index.as_query_engine()

## Get a Response

In [9]:
response = query_engine.query("What are these files about?")

print(response)
print(response.metadata)

 These files appear to be related to a real estate transaction involving multiple properties with different addresses in Cedar Park and San Antonio, Texas. The documents contain details such as property addresses, legal descriptions, purchase prices, loan amounts, and the names of involved parties like buyers, sellers, and settlement agencies.
{'596b3b27-9546-49b4-aae9-1987ce11e099': {'page_label': '2', 'file_name': 'Test.pdf', 'file_path': 'data/Test.pdf', 'file_type': 'application/pdf', 'file_size': 117715, 'creation_date': '2023-11-27', 'last_modified_date': '2023-11-10', 'last_accessed_date': '2023-11-27'}, '1f3342ca-d98d-4217-b7d1-d6dc83baa36b': {'page_label': '1', 'file_name': 'Test.pdf', 'file_path': 'data/Test.pdf', 'file_type': 'application/pdf', 'file_size': 117715, 'creation_date': '2023-11-27', 'last_modified_date': '2023-11-10', 'last_accessed_date': '2023-11-27'}}



llama_print_timings:        load time =     155.73 ms
llama_print_timings:      sample time =       8.36 ms /    63 runs   (    0.13 ms per token,  7534.08 tokens per second)
llama_print_timings: prompt eval time =     480.62 ms /  1289 tokens (    0.37 ms per token,  2681.97 tokens per second)
llama_print_timings:        eval time =     769.75 ms /    62 runs   (   12.42 ms per token,    80.55 tokens per second)
llama_print_timings:       total time =    1315.94 ms
